In [ ]:
import datetime
from dateutil import parser
import pyodbc as db
import pandas as pd

In [2]:
conn = db.connect(
    'Driver={ODBC Driver 17 for SQL Server};'
    'Server=Athul;'
    'DATABASE=mbta;'
    'Trusted_Connection=yes;',
    autocommit=True
)
conn.setdecoding(db.SQL_CHAR, encoding='latin1')
conn.setencoding('latin1')
cursor = conn.cursor()
print("connected to mbta database")

connected to mbta database


In [3]:
def load_directions_ids():
    df = pd.read_csv('vehicles-direction_ids.csv',keep_default_na=False)
    print(df.head())
    
    cursor.execute("SELECT COUNT(*) FROM directions")

    for index, row in df.iterrows():
        direction = str(row['direction_ids'])
        cursor.execute("SELECT direction FROM directions WHERE direction = ?", (direction,))
        exists = cursor.fetchone()

        if not exists:
            cursor.execute("INSERT INTO directions (direction) VALUES (?)", (direction,))

    conn.commit()

load_directions_ids()

  direction_ids
0             0
1          None
2             1
3             2


In [4]:
def load_routes_direction_names():
    df = pd.read_csv(
        'routes-direction_names.csv',
    )

    for index, row in df.iterrows():
        direction_name = row['direction_names']
        print(f"{direction_name}")

        cursor.execute("SELECT direction_name FROM direction_names WHERE direction_name = ?", (direction_name,))
        exists = cursor.fetchone()

        if not exists:
            cursor.execute("INSERT INTO direction_names (direction_name) VALUES (?)", (direction_name,))

    conn.commit()

load_routes_direction_names()


Inbound
East
Outbound
North
West
South


In [5]:
def load_destinations():
    df = pd.read_csv(
        'routes-direction_destinations.csv'
    )

    for index, row in df.iterrows():
        destination = row['direction_destinations']
        print(f"{destination}")

        cursor.execute("SELECT destination FROM destinations WHERE destination = ?", (destination,))
        exists = cursor.fetchone()

        if not exists:
            cursor.execute("INSERT INTO destinations (destination) VALUES (?)", (destination,))
    conn.commit()

load_destinations()


Central Wharf
Turkey Hill
Elm Street
Oak Grove
Braintree Station
Harvard Station
Federal Street & Franklin Street
Cobbs Corner
Woodlawn
Medford Square
Nubian Station
Back Bay Station
North Waltham
University Park
South Shore Plaza
Forge Park/495 or Foxboro
South Station
Harvard
Stoughton or Wickford Junction
Kendall/MIT Station
Millennium Park or VA Hospital
Government Center
Kenmore Station
Watertown Yard
Brighton Center
Reading Depot
Wolcott or Cleary Square
Orient Heights Station
Clarendon Hill or Arlington Center
Forest Hills Station
Long Wharf
Lowell
Hingham or Hull
Arlmont Village
West Medford or Arlington Center
Beth Israel Deaconess Hospital
Needham Junction
Kingston
Watertown Square
North Woburn
North Burlington
Wonderland Station
Boston College
Quincy
Centre Street & Eliot Street
Park Street Station
Waltham Highlands
Spring Hill
Clarendon Hill or Davis Station
Waverley Square
Cleveland Circle
Pemberton Point, Hull
Haymarket or Wonderland Station
Waltham Center
Baker Street & 

In [6]:
def load_colors():
    lines_df = pd.read_csv('lines.csv')
    lines_colors = pd.unique(
        pd.concat([lines_df['color'], lines_df['text_color']])
    )
    print(f"lines: {lines_colors}")
    routes_df = pd.read_csv('routes.csv')
    routes_colors = pd.unique(
        pd.concat([routes_df['color'], routes_df['text_color']])
    )
    print(f"route: {routes_colors}")
    all_colors = pd.Series(list(lines_colors) + list(routes_colors)).drop_duplicates()

    for color in all_colors:
        cursor.execute("SELECT color FROM colors WHERE color = ?", (color,))
        exists = cursor.fetchone()

        if not exists:
            cursor.execute("INSERT INTO colors (color) VALUES (?)", (color,))
    conn.commit()

load_colors()

lines: ['DA291C' 'ED8B00' '00843D' '003DA5' '7C878E' '80276C' '006595' '008EAA'
 'FFC72C' 'FFFFFF' '000000']
route: ['DA291C' 'ED8B00' '00843D' '003DA5' '7C878E' '80276C' '008EAA' 'FFC72C'
 'FFFFFF' '000000']


In [7]:
def load_lines():
    lines_df = pd.read_csv('lines.csv',  dtype=str)
    routes_df = pd.read_csv('routes.csv',  dtype=str)

    print(f" {len(lines_df)} lines, {len(routes_df)} routes")

    # Load from lines.csv
    for _, row in lines_df.iterrows():
        line_id = row['id']

        cursor.execute("SELECT line_id FROM lines WHERE line_id = ?", (line_id,))
        if cursor.fetchone():
            continue

        # Get color_id
        cursor.execute("SELECT color_id FROM colors WHERE color = ?", (row['color'],))
        color = cursor.fetchone()
        if not color:
            continue

        cursor.execute("SELECT color_id FROM colors WHERE color = ?", (row['text_color'],))
        text_color = cursor.fetchone()
        if not text_color:
            continue
        print((line_id, color[0], str(row['long_name']) if not pd.isna(row['long_name']) else '', str(row['short_name']) if not pd.isna(row['short_name']) else '', text_color[0]))
        cursor.execute("""
            INSERT INTO lines (line_id, color, long_name, short_name, text_color)
            VALUES (?, ?, ?, ?, ?)
        """, (
                str(line_id),
                int(color[0]),
                str(row['long_name']) if not pd.isna(row['long_name']) else '',
                str(row['short_name']) if not pd.isna(row['short_name']) else '',
                int(text_color[0])
            ))

    # Load from routes.csv (if line_id not already added)
    for _, row in routes_df.iterrows():
        line_id = row['line_id']
        if line_id == '':
            continue

        cursor.execute("SELECT line_id FROM lines WHERE line_id = ?", (line_id,))
        if cursor.fetchone():
            continue

        cursor.execute("SELECT color_id FROM colors WHERE color = ?", (row['color'],))
        color = cursor.fetchone()
        if not color:
            continue

        cursor.execute("SELECT color_id FROM colors WHERE color = ?", (row['text_color'],))
        text_color = cursor.fetchone()
        if not text_color:
            continue

        cursor.execute("""
            INSERT INTO lines (line_id, color, long_name, short_name, text_color)
            VALUES (?, ?, ?, ?, ?)
        """, (
                str(line_id),
                int(color[0]),
                str(row['long_name']) if not pd.isna(row['long_name']) else '',
                str(row['short_name']) if not pd.isna(row['short_name']) else '',
                int(text_color[0])
            ))

    conn.commit()

load_lines()


 142 lines, 178 routes


In [8]:
def load_routes():
    df = pd.read_csv('routes.csv', dtype=str)
    print(f"{len(df)} routes")

    for _, row in df.iterrows():
        route_id = row['id']

        cursor.execute("SELECT route_id FROM routes WHERE route_id = ?", (route_id,))
        if cursor.fetchone():
            continue

        # Get color ID
        cursor.execute("SELECT color_id FROM colors WHERE color = ?", (row['color'],))
        color = cursor.fetchone()
        if not color:
            continue

        # Get text_color ID
        cursor.execute("SELECT color_id FROM colors WHERE color = ?", (row['text_color'],))
        text_color = cursor.fetchone()
        if not text_color:
            continue

        # Check for line_id
        if row['line_id'].strip() != '':
            cursor.execute("SELECT line_id FROM lines WHERE line_id = ?", (row['line_id'],))
            found = cursor.fetchone()
            if found:
                line_id = found[0]

        # Insert into routes
        if line_id:
            print((
                str(route_id), color[0], row['description'], row['fare_class'],
                str(row['long_name']) if not pd.isna(row['short_name']) else '', str(row['short_name']) if not pd.isna(row['short_name']) else '', text_color[0], line_id
            ))
            cursor.execute("""
                INSERT INTO routes (route_id, color, description, fare_class, long_name, short_name, text_color, line_id)
                VALUES (?, ?, ?, ?, ?, ?, ?, ?)
            """, (
                str(route_id), color[0], row['description'], row['fare_class'],
                str(row['long_name']) if not pd.isna(row['short_name']) else '', str(row['short_name']) if not pd.isna(row['short_name']) else '', text_color[0], line_id
            ))
        else:
            cursor.execute("""
                INSERT INTO routes (route_id, color, description, fare_class, long_name, short_name, text_color)
                VALUES (?, ?, ?, ?, ?, ?, ?)
            """, (
                str(route_id), color[0], row['description'], row['fare_class'],
                str(row['long_name']) if not pd.isna(row['short_name']) else '', str(row['short_name']) if not pd.isna(row['short_name']) else '', text_color[0]
            ))

    conn.commit()

load_routes()


178 routes


In [9]:
def load_direction_names_routes_bridge():
    # direction_name_ids
    direction_names_df = pd.read_sql("SELECT direction_name_id FROM direction_names", conn)
    print(direction_names_df.head())
    # route_ids
    routes_df = pd.read_sql("SELECT route_id FROM routes", conn)
    print(routes_df.head())

    for _, route_row in routes_df.iterrows():
        for _, dir_row in direction_names_df.iterrows():
            route_id = str(route_row['route_id'])
            direction_name_id = int(dir_row['direction_name_id'])
            print(f"Inserting route_id: {route_id}, direction_name_id: {direction_name_id}")

            cursor.execute("""
                SELECT 1 FROM direction_names_routes_bridge
                WHERE route_id = ? AND direction_name_id = ?
            """, (route_id, direction_name_id))
            exists = cursor.fetchone()

            if not exists:
                cursor.execute("""
                    INSERT INTO direction_names_routes_bridge (route_id, direction_name_id)
                    VALUES (?, ?)
                """, (route_id, direction_name_id))

    conn.commit()

load_direction_names_routes_bridge()

   direction_name_id
0                  2
1                  1
2                  4
3                  3
4                  6
  route_id
0        1
1       10
2      100
3      101
4      104
Inserting route_id: 1, direction_name_id: 2
Inserting route_id: 1, direction_name_id: 1
Inserting route_id: 1, direction_name_id: 4
Inserting route_id: 1, direction_name_id: 3
Inserting route_id: 1, direction_name_id: 6
Inserting route_id: 1, direction_name_id: 5
Inserting route_id: 10, direction_name_id: 2
Inserting route_id: 10, direction_name_id: 1
Inserting route_id: 10, direction_name_id: 4
Inserting route_id: 10, direction_name_id: 3
Inserting route_id: 10, direction_name_id: 6
Inserting route_id: 10, direction_name_id: 5
Inserting route_id: 100, direction_name_id: 2
Inserting route_id: 100, direction_name_id: 1
Inserting route_id: 100, direction_name_id: 4
Inserting route_id: 100, direction_name_id: 3
Inserting route_id: 100, direction_name_id: 6
Inserting route_id: 100, direction_name_id: 

C:\Users\athul\AppData\Local\Temp\ipykernel_29016\1776480674.py:3: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  direction_names_df = pd.read_sql("SELECT direction_name_id FROM direction_names", conn)
C:\Users\athul\AppData\Local\Temp\ipykernel_29016\1776480674.py:6: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  routes_df = pd.read_sql("SELECT route_id FROM routes", conn)


In [10]:
def load_destinations_routes_bridge():
    # Get all destination_ids
    cursor.execute("SELECT destination_id FROM destinations")
    destination_ids = cursor.fetchall()
    # print(f"Destination IDs: {destination_ids}")

    # Get all route_ids
    cursor.execute("SELECT route_id FROM routes")
    route_ids = cursor.fetchall()
    # print(f"Route IDs: {route_ids}")

    # Bridge insert if not already connected
    for route_id in route_ids:
        for destination_id in destination_ids:
            cursor.execute("""
                SELECT 1 FROM destinations_routes_bridge
                WHERE route_id = ? AND destination_id = ?
            """, route_id[0], destination_id[0])
            exists = cursor.fetchone()

            if not exists:
                cursor.execute("""
                    INSERT INTO destinations_routes_bridge (route_id, destination_id)
                    VALUES (?, ?)
                """, route_id[0], destination_id[0])
load_destinations_routes_bridge()

In [ ]:
def load_destinations_routes_bridge():
    # Get all destination_ids
    destination_df = pd.read_sql("SELECT destination_id FROM destinations", conn)
    print(destination_df.head())
    # Get all route_ids
    route_df = pd.read_sql("SELECT route_id FROM routes", conn)
    print(route_df.head())
    
    for _, route_row in route_df.iterrows():
        for _, dest_row in destination_df.iterrows():
            route_id = str(route_row['route_id'])
            destination_id = int(dest_row['destination_id'])

            print("running till before select")
            cursor.execute("""
                SELECT 1 FROM destinations_routes_bridge
                WHERE route_id = ? AND destination_id = ?
            """, (route_id, destination_id))
            exists = cursor.fetchone()
            if not exists:
                cursor.execute("""
                    INSERT INTO destinations_routes_bridge (route_id, destination_id)
                    VALUES (?, ?)
                """, (route_id, destination_id))
    conn.commit()

load_destinations_routes_bridge()


C:\Users\athul\AppData\Local\Temp\ipykernel_29016\2084494552.py:3: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  destination_df = pd.read_sql("SELECT destination_id FROM destinations", conn)
C:\Users\athul\AppData\Local\Temp\ipykernel_29016\2084494552.py:6: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  route_df = pd.read_sql("SELECT route_id FROM routes", conn)


   destination_id
0              72
1             176
2             174
3             121
4             138
  route_id
0        1
1       10
2      100
3      101
4      104
running till before select
running till after select
running till after insert
running till before select
running till after select
running till after insert
running till before select
running till after select
running till after insert
running till before select
running till after select
running till after insert
running till before select
running till after select
running till after insert
running till before select
running till after select
running till after insert
running till before select
running till after select
running till after insert
running till before select
running till after select
running till after insert
running till before select
running till after select
running till after insert
running till before select
running till after select
running till after insert
running till before select
running t

In [12]:
def load_municipalities():
    df = pd.read_csv('stops.csv', dtype=str)
    print(df.head())

    for _, row in df.iterrows():
        municipality = row.iloc[6]  # column index 6 from your original logic
        print(f"Processing municipality: {municipality}")
        
        cursor.execute("SELECT municipality_id FROM municipalities WHERE municipality = ?", (municipality,))
        exists = cursor.fetchone()

        if not exists:
            cursor.execute("INSERT INTO municipalities (municipality) VALUES (?)", (municipality,))

    conn.commit()

load_municipalities()


     id address       at_street description   latitude   longitude  \
0  7954     NaN   Candia Street         NaN  42.425213  -71.168978   
1  7578     NaN             NaN         NaN  42.383979  -71.210523   
2  2231     NaN             NaN         NaN  42.362498  -71.085841   
3  1521     NaN             NaN         NaN   42.33851  -71.107918   
4  2329     NaN  Radcliffe Road         NaN     42.409  -71.174303   

  municipality                                  name          on_street  
0    Arlington             Washington St @ Candia St  Washington Street  
1      Waltham          Beaver St @ Waverley Oaks Rd      Beaver Street  
2    Cambridge  Main St @ Kendall Station - Red Line        Main Street  
3       Boston          Brookline Ave @ Longwood Ave   Brookline Avenue  
4      Belmont        East Service Rd @ Radcliffe Rd      Frontage Road  
Processing municipality: Arlington
Processing municipality: Waltham
Processing municipality: Cambridge
Processing municipality: Boston


In [ ]:
def load_streets():
    df = pd.read_csv('stops.csv', dtype=str, keep_default_na=False)
    print(df.head())

    for _, row in df.iterrows():
        at_street = row.iloc[2]
        print(f"Processing at_street: {at_street}")
        on_street = row.iloc[8]
        print(f"Processing on_street: {on_street}")

        # Insert at street if non-empty and doesn't exist
        if at_street.strip():
            cursor.execute("SELECT street FROM streets WHERE street = ?", (at_street,))
            exists = cursor.fetchone()
            if not exists:
                cursor.execute("INSERT INTO streets (street) VALUES (?)", (at_street,))

        # Insert on street if non-empty and doesn't exist
        if on_street.strip():
            cursor.execute("SELECT street FROM streets WHERE street = ?", (on_street,))
            exists = cursor.fetchone()
            if not exists:z
                cursor.execute("INSERT INTO streets (street) VALUES (?)", (on_street,))

    conn.commit()

load_streets()


     id address       at_street description   latitude   longitude  \
0  7954           Candia Street              42.425213  -71.168978   
1  7578                                      42.383979  -71.210523   
2  2231                                      42.362498  -71.085841   
3  1521                                       42.33851  -71.107918   
4  2329          Radcliffe Road                 42.409  -71.174303   

  municipality                                  name          on_street  
0    Arlington             Washington St @ Candia St  Washington Street  
1      Waltham          Beaver St @ Waverley Oaks Rd      Beaver Street  
2    Cambridge  Main St @ Kendall Station - Red Line        Main Street  
3       Boston          Brookline Ave @ Longwood Ave   Brookline Avenue  
4      Belmont        East Service Rd @ Radcliffe Rd      Frontage Road  
Processing at_street: Candia Street
Processing on_street: Washington Street
Processing at_street: 
Processing on_street: Beaver Street


In [15]:
def load_stops():
    df = pd.read_csv('stops.csv', dtype=str, keep_default_na=False)
    print(df.head())

    for _, row in df.iterrows():
        print(row.tolist())
        stop_id = row.iloc[0]
        address = row.iloc[1]
        at_street_name = row.iloc[2]
        description = row.iloc[3]
        latitude = row.iloc[4]
        longitude = row.iloc[5]
        municipality_name = row.iloc[6]
        name = row.iloc[7]
        on_street_name = row.iloc[8]

        cursor.execute("SELECT stop_id FROM stops WHERE stop_id = ?", (stop_id,))
        exists = cursor.fetchone()

        if exists:
            continue

        # Get municipality_id
        cursor.execute("SELECT municipality_id FROM municipalities WHERE municipality = ?", (municipality_name,))
        municipality = cursor.fetchone()
        if not municipality:
            continue
        municipality_id = municipality[0]

        # Get at_street and on_street IDs
        cursor.execute("SELECT street_id FROM streets WHERE street = ?", (at_street_name,))
        at_street = cursor.fetchone()

        cursor.execute("SELECT street_id FROM streets WHERE street = ?", (on_street_name,))
        on_street = cursor.fetchone()

        # Insert based on which street(s) exist
        if not at_street and on_street:
            cursor.execute("""
                INSERT INTO stops (stop_id, address, description, latitude, longitude, municipality_id, name, on_street)
                VALUES (?, ?, ?, ?, ?, ?, ?, ?)
            """, (stop_id, address, description, latitude, longitude, municipality_id, name, on_street[0]))

        elif not on_street and at_street:
            cursor.execute("""
                INSERT INTO stops (stop_id, address, at_street, description, latitude, longitude, municipality_id, name)
                VALUES (?, ?, ?, ?, ?, ?, ?, ?)
            """, (stop_id, address, at_street[0], description, latitude, longitude, municipality_id, name))

        else:
            cursor.execute("""
                INSERT INTO stops (stop_id, address, description, latitude, longitude, municipality_id, name)
                VALUES (?, ?, ?, ?, ?, ?, ?)
            """, (stop_id, address, description, latitude, longitude, municipality_id, name))

    conn.commit()

load_stops()


     id address       at_street description   latitude   longitude  \
0  7954           Candia Street              42.425213  -71.168978   
1  7578                                      42.383979  -71.210523   
2  2231                                      42.362498  -71.085841   
3  1521                                       42.33851  -71.107918   
4  2329          Radcliffe Road                 42.409  -71.174303   

  municipality                                  name          on_street  
0    Arlington             Washington St @ Candia St  Washington Street  
1      Waltham          Beaver St @ Waverley Oaks Rd      Beaver Street  
2    Cambridge  Main St @ Kendall Station - Red Line        Main Street  
3       Boston          Brookline Ave @ Longwood Ave   Brookline Avenue  
4      Belmont        East Service Rd @ Radcliffe Rd      Frontage Road  
['7954', '', 'Candia Street', '', '42.425213', '-71.168978', 'Arlington', 'Washington St @ Candia St', 'Washington Street']
['7578', ''

In [ ]:
def load_statuses():
    df = pd.read_csv('vehicles-current_statuses.csv', dtype=str, keep_default_na=False)
    print(df.head())

    for _, row in df.iterrows():
        status = row.iloc[0]
        print(f"Processing status: {status}")
        
        cursor.execute("SELECT status FROM statuses WHERE status = ?", (status,))
        exists = cursor.fetchone()

        if not exists:
            cursor.execute("INSERT INTO statuses (status) VALUES (?)", (status,))

    conn.commit()

load_statuses()


  current_statuses
0    IN_TRANSIT_TO
1       STOPPED_AT
2      INCOMING_AT
Processing status: IN_TRANSIT_TO
Processing status: STOPPED_AT
Processing status: INCOMING_AT


In [ ]:
def load_vehicles_data():
    df = pd.read_csv('vehicles.csv', quotechar='"', dtype=str, keep_default_na=False)
    print(df.head())

    # Calculate UTC offset
    local_now = datetime.datetime.now().astimezone()
    utc_now = datetime.datetime.now(datetime.timezone.utc)
    utc_delta = utc_now - local_now


    for _, row in df.iterrows():
        try:
            # Parse and format updated_at
            updated_at = parser.parse(row.iloc[8]) + utc_delta
            updated_at = updated_at.strftime('%Y-%m-%d %H:%M:%S')

            # Check if vehicle record already exists
            cursor.execute("""
                SELECT vehicle_id, updated_at 
                FROM vehicles_data 
                WHERE vehicle_id = ? AND updated_at = ?
            """, (row.iloc[0], updated_at))
            exists = cursor.fetchone()

            if exists:
                continue

            # Get foreign keys
            cursor.execute("SELECT direction_id FROM directions WHERE direction = ?", (row.iloc[4],))
            direction_id = cursor.fetchone()[0]

            try:
                cursor.execute("SELECT route_id FROM routes WHERE route_id = ?", (row.iloc[10],))
                route_id = cursor.fetchone()[0]
            except TypeError:
                print(f'ROUTE_ID "{row.iloc[10]}" does not exist in ROUTES table - ignoring')
                continue

            cursor.execute("SELECT stop_id FROM stops WHERE stop_id = ?", (row.iloc[11],))
            stop_id = cursor.fetchone()

            cursor.execute("SELECT status_id FROM statuses WHERE status = ?", (row.iloc[9],))
            status_id = cursor.fetchone()[0]

            speed = row.iloc[7] if row.iloc[7] not in ['None', ''] else ''
            current_stop_sequence = row.iloc[3] if row.iloc[3] not in ['None', ''] else ''
            bearing = row.iloc[2] if row.iloc[2] not in ['None', ''] else ''
            print(f"Processing vehicle_id: {row.iloc[0]}, updated_at: {updated_at}, direction_id: {direction_id}, route_id: {route_id}, stop_id: {stop_id}, status_id: {status_id}")
            
            if not stop_id:
                cursor.execute("""
                    INSERT INTO vehicles_data (
                        vehicle_id, label, bearing, current_stop_sequence,
                        longitude, latitude, speed, updated_at,
                        direction_id, route_id, current_status
                    )
                    VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
                """, (
                    row.iloc[0], row.iloc[1], bearing, current_stop_sequence,
                    row.iloc[5], row.iloc[6], speed, updated_at,
                    direction_id, route_id, status_id
                ))
            else:
                cursor.execute("""
                    INSERT INTO vehicles_data (
                        vehicle_id, label, bearing, current_stop_sequence,
                        longitude, latitude, speed, updated_at,
                        direction_id, route_id, current_status, stop_id
                    )
                    VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
                """, (
                    row.iloc[0], row.iloc[1], bearing, current_stop_sequence,
                    row.iloc[5], row.iloc[6], speed, updated_at,
                    direction_id, route_id, status_id, stop_id[0]
                ))

        except Exception as e:
            print(f"vehicle_id {row.iloc[0]}: {e}")

    conn.commit()

load_vehicles_data()


        id   label bearing current_stop_sequence direction_id     longitude  \
0    y0892    0892     335                    28            0   -71.1313264   
1    y3278    3278      74                     2            0  -71.09693711   
2    y1337    1337     315                     1            0  -71.05540138   
3  dLF 958  LF 958     330                    10            0  -70.87287023   
4    y3151    3151     309                     3            0  -71.08962148   

      latitude speed                 updated_at current_status route_id  \
0  42.43223074  None  2025-05-01T10:38:58-04:00     STOPPED_AT      134   
1  42.34876894  None  2025-05-01T10:38:52-04:00  IN_TRANSIT_TO       57   
2  42.35248277  None  2025-05-01T10:35:52-04:00     STOPPED_AT      741   
3  42.28169965  None  2025-05-01T10:38:16-04:00  IN_TRANSIT_TO      714   
4  42.36482998  None  2025-05-01T10:38:54-04:00  IN_TRANSIT_TO       68   

  stop_id  
0    8692  
1     951  
2   74611  
3  111864  
4   24486  
Pr